In [1]:
import requests
import json
import numpy as np
import pandas as pd
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

In [13]:
df = pd.read_csv('./dataforthai.csv', dtype={'tax':str, 'tsic':str})
df

no   tsic            tax  \
0            0   1111  0245560002150   
1            1   1111  0405562003771   
2            2   1111  0105554033902   
3            3   1111  0303564003395   
4            4   1111  0303564003409   
...        ...    ...            ...   
863538  863538  98100   105565163055   
863539  863539  98100   125558010842   
863540  863540  98100   105565036606   
863541  863541  99000   105558183798   
863542  863542  99009   303559004753   

                                          name_th  \
0                บริษัท กรีนแพลนท์ อินเตอร์ จำกัด   
1           บริษัท แอทเทนด์ แพลนท์ เทรดดิ้ง จำกัด   
2                       บริษัท แอท การ์เด้น จำกัด   
3       ห้างหุ้นส่วนจำกัด สำเริงรุ่งโรจน์การเกษตร   
4                   ห้างหุ้นส่วนจำกัด สวนเคียงคอน   
...                                           ...   
863538        บริษัท เอ พี ที บูสเตอร์ ปั๊ม จำกัด   
863539                      บริษัท อะโบฟ 29 จำกัด   
863540                    บริษัท ฟ็อกซ์บุรี จำกัด   
863541          บริษัท อัล- ระยาน เฮลท์แคร์ จำกัด   
863542                  ห้างหุ้นส่วนจำกัด ธนพล 08   

                                               name_en  \
0                    GREENPLANTS INTER COMPANY LIMITED   
1                 ATTEND PLANT TRADING COMPANY LIMITED   
2                            AT GARDEN COMPANY LIMITED   
3       SAMROENG RUNGROJ KARNKASET LIMITED PARTNERSHIP   
4                                                    -   
...                                                ...   
863538                                               -   
863539                                               -   
863540                                               -   
863541                                               -   
863542                                               -   

                                                 business  \
0              การขายส่งวัตถุดิบทางการเกษตรและสิ่งมีชีวิต   
1       ปลูกข้าวโพดทานสด ข้าวโพดทานดิบและข้าวโพดประเภท...   
2       ประกอบกิจการจำหน่ายพืชผลทางการเกษตรทุกชนิด ทำป...   
3       ประกอบกิจการเพาะปลูก และค้าผลผลิตจากข้าวโพดตาม...   
4                                                       -   
...                                                   ...   
863538                                                  -   
863539                                                  -   
863540                                                  -   
863541                                                  -   
863542                                                  -   

                     status date_register_thai        capital  \
0       ยังดำเนินกิจการอยู่    14 กรกฎาคม 2560  1,000,000 บาท   
1       ยังดำเนินกิจการอยู่    21 สิงหาคม 2562  1,000,000 บาท   
2       ยังดำเนินกิจการอยู่      9 มีนาคม 2554  1,000,000 บาท   
3       ยังดำเนินกิจการอยู่      5 เมษายน 2564    500,000 บาท   
4                         -                  -              -   
...                     ...                ...            ...   
863538                    -                  -              -   
863539                    -                  -              -   
863540                    -                  -              -   
863541                    -                  -              -   
863542                    -                  -              -   

                                                  address  \
0       325 หมู่ที่ 6 ตำบลท่าตะเกียบ อำเภอท่าตะเกียบ จ...   
1       222/16 หมู่ที่ 16 ถนนมะลิวัลย์ ตำบลบ้านเป็ด อำ...   
2       511/2 ซอยลาดพร้าว 94 แขวงพลับพลา เขตวังทองหลาง...   
3       66 หมู่ที่ 2 ตำบลตะแบกบาน อำเภอครบุรี จ.นครราช...   
4                                                       -   
...                                                   ...   
863538                                                  -   
863539                                                  -   
863540                                                  -   
863541                                                  -   
863542      

In [3]:
### PAYLOAD & COOKIES FOR LOGING TO DATAFORTHAI
payload = {"mode": "login", "member_type": "2", "username": "onlyaeddie@gmail.com",
                   "password": "AdnAbl221199", "rc": "8312c16366f2e01e9a25547a15605fdd"}
cookies={"PHPSESSID": "4va2r65lse8q43jotece5k1njn"}

In [ ]:
### PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if v[1]['name_en'] != '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        df['status'].iloc[i] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        df['date_register_thai'].iloc[i] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        df['capital'].iloc[i] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        df['address'].iloc[i] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        df['list_committee'].iloc[i] = list_committee + list_committee_other
        
        df.to_csv('./dataforthai.csv', encoding='utf-8', index=False, )


In [5]:
df

no   tsic            tax  \
0            0   1111  0245560002150   
1            1   1111  0405562003771   
2            2   1111  0105554033902   
3            3   1111  0303564003395   
4            4   1111  0303564003409   
...        ...    ...            ...   
863538  863538  98100   105565163055   
863539  863539  98100   125558010842   
863540  863540  98100   105565036606   
863541  863541  99000   105558183798   
863542  863542  99009   303559004753   

                                          name_th  \
0                บริษัท กรีนแพลนท์ อินเตอร์ จำกัด   
1           บริษัท แอทเทนด์ แพลนท์ เทรดดิ้ง จำกัด   
2                       บริษัท แอท การ์เด้น จำกัด   
3       ห้างหุ้นส่วนจำกัด สำเริงรุ่งโรจน์การเกษตร   
4                   ห้างหุ้นส่วนจำกัด สวนเคียงคอน   
...                                           ...   
863538        บริษัท เอ พี ที บูสเตอร์ ปั๊ม จำกัด   
863539                      บริษัท อะโบฟ 29 จำกัด   
863540                    บริษัท ฟ็อกซ์บุรี จำกัด   
863541          บริษัท อัล- ระยาน เฮลท์แคร์ จำกัด   
863542                  ห้างหุ้นส่วนจำกัด ธนพล 08   

                                               name_en  \
0                    GREENPLANTS INTER COMPANY LIMITED   
1                 ATTEND PLANT TRADING COMPANY LIMITED   
2                            AT GARDEN COMPANY LIMITED   
3       SAMROENG RUNGROJ KARNKASET LIMITED PARTNERSHIP   
4                                                    -   
...                                                ...   
863538                                               -   
863539                                               -   
863540                                               -   
863541                                               -   
863542                                               -   

                                                 business  \
0              การขายส่งวัตถุดิบทางการเกษตรและสิ่งมีชีวิต   
1       ปลูกข้าวโพดทานสด ข้าวโพดทานดิบและข้าวโพดประเภท...   
2       ประกอบกิจการจำหน่ายพืชผลทางการเกษตรทุกชนิด ทำป...   
3       ประกอบกิจการเพาะปลูก และค้าผลผลิตจากข้าวโพดตาม...   
4                                                       -   
...                                                   ...   
863538                                                  -   
863539                                                  -   
863540                                                  -   
863541                                                  -   
863542                                                  -   

                     status date_register_thai        capital  \
0       ยังดำเนินกิจการอยู่    14 กรกฎาคม 2560  1,000,000 บาท   
1       ยังดำเนินกิจการอยู่    21 สิงหาคม 2562  1,000,000 บาท   
2       ยังดำเนินกิจการอยู่      9 มีนาคม 2554  1,000,000 บาท   
3       ยังดำเนินกิจการอยู่      5 เมษายน 2564    500,000 บาท   
4                         -                  -              -   
...                     ...                ...            ...   
863538                    -                  -              -   
863539                    -                  -              -   
863540                    -                  -              -   
863541                    -                  -              -   
863542                    -                  -              -   

                                                  address  \
0       325 หมู่ที่ 6 ตำบลท่าตะเกียบ อำเภอท่าตะเกียบ จ...   
1       222/16 หมู่ที่ 16 ถนนมะลิวัลย์ ตำบลบ้านเป็ด อำ...   
2       511/2 ซอยลาดพร้าว 94 แขวงพลับพลา เขตวังทองหลาง...   
3       66 หมู่ที่ 2 ตำบลตะแบกบาน อำเภอครบุรี จ.นครราช...   
4                                                       -   
...                                                   ...   
863538                                                  -   
863539                                                  -   
863540                                                  -   
863541                                                  -   
863542      

# Code in Production

In [ ]:
#Group all the upper code
import requests
import json
import numpy as np
import pandas as pd
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

df = pd.read_csv('./dataforthai.csv', dtype={'tax':str, 'tsic':str})

# PAYLOAD & COOKIES FOR LOGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if v[1]['name_en'] != '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        df['status'].iloc[i] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        df['date_register_thai'].iloc[i] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        df['capital'].iloc[i] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        df['address'].iloc[i] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        df['list_committee'].iloc[i] = list_committee + list_committee_other
        
        df.to_csv('./dataforthai.csv', encoding='utf-8', index=False, )

In [3]:
# Scrape without proxy
import requests
import json
import numpy as np
import pandas as pd
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

df = pd.read_csv('./dataforthai.csv', dtype={'tax': str, 'tsic': str})

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies= {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if i == 25:
        break
    
    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        df['status'].iloc[i] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        df['date_register_thai'].iloc[i] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        df['capital'].iloc[i] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        df['address'].iloc[i] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        df['list_committee'].iloc[i] = list_committee + list_committee_other

        df.to_csv('./dataforthai_test.csv', encoding='utf-8', index=False)


C:\Users\Warit\AppData\Local\Temp\ipykernel_22156\2554658715.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
C:\Users\Warit\AppData\Local\Temp\ipykernel_22156\2554658715.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
C:\Users\Warit\AppData\Local\Temp\ipykernel_22156\2554658715.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.

In [2]:
#Read and Update i
import requests
import json
import numpy as np
import pandas as pd
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

df = pd.read_csv('./dataforthai_test.csv', dtype={'tax': str, 'tsic': str})

# File path to store and load the value of 'i'
index_file = './last_index.txt'

# Load the last index value if the file exists
try:
    with open(index_file, 'r') as file:
        last_index = int(file.read().strip())
except FileNotFoundError:
    last_index = None

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if i == 50:
        break

    if last_index is not None and i <= last_index:
        continue
    
    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        df['status'].iloc[i] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        df['date_register_thai'].iloc[i] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        df['capital'].iloc[i] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        df['address'].iloc[i] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        df['list_committee'].iloc[i] = list_committee + list_committee_other

        df.to_csv('./dataforthai_test.csv', encoding='utf-8', index=False)
        
        # Save the current index value to the file
        with open(index_file, 'w') as file:
            file.write(str(i))

KeyboardInterrupt: 

In [1]:
#Read i and CAPPED it
import requests
import json
import numpy as np
import pandas as pd
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

df = pd.read_csv('./dataforthai_test2.csv', dtype={'tax': str, 'tsic': str})

# File path to store and load the value of 'i'
index_file = './last_index.txt'

# Load the last index value if the file exists
try:
    with open(index_file, 'r') as file:
        last_index = int(file.read().strip())
except FileNotFoundError:
    last_index = None

# Set the parameter value as the sum of 'i' and 25
break_parameter = last_index + 15 if last_index is not None else None

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if last_index is not None and i <= last_index:
        continue
    
    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        df['status'].iloc[i] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        df['date_register_thai'].iloc[i] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        df['capital'].iloc[i] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        df['address'].iloc[i] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        df['list_committee'].iloc[i] = list_committee + list_committee_other

        df.to_csv('./dataforthai_test2.csv', encoding='utf-8', index=False)
        
        # Save the current index value to the file
        with open(index_file, 'w') as file:
            file.write(str(i))

        # Check if the break condition is met
        if i == break_parameter:
            break


C:\Users\Warit\AppData\Local\Temp\ipykernel_26100\195315054.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
C:\Users\Warit\AppData\Local\Temp\ipykernel_26100\195315054.py:43: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
C:\Users\Warit\AppData\Local\Temp\ipykernel_26100\195315054.py:44: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pyd

AttributeError: 'NoneType' object has no attribute 'strip'

In [1]:
#Optimized
import requests
import json
import numpy as np
import pandas as pd
import time
import random
from parsel import Selector
from datetime import datetime

df = pd.read_csv('./dataforthai_test2.csv', dtype={'tax': str, 'tsic': str})

# File path to store and load the value of 'i'
index_file = './last_index.txt'

# Load the last index value if the file exists
try:
    with open(index_file, 'r') as file:
        last_index = int(file.read().strip())
except FileNotFoundError:
    last_index = None

# Set the parameter value as the sum of 'i' and 25
break_parameter = last_index + 15 if last_index is not None else None

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "e4t0k89bfc1t7jmd2anr72umde"}

# Create a session object for HTTP requests
session = requests.Session()

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if last_index is not None and i <= last_index:
        continue
    
    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        url = f'https://dataforthai.com/company/{tax}/'
        
        # Use the session object for the request
        req = session.get(url, cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        df.at[i, 'name_en'] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        df.at[i, 'business'] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        df.at[i, 'status'] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        df.at[i, 'date_register_thai'] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        df.at[i, 'capital'] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        address_element = container_body.xpath('//*/table[6]/tr/td[2]/a/text()')
        df.at[i, 'address'] = address_element.get().strip() if address_element else ""
        
        # Use list comprehension for committee lists
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        df.at[i, 'list_committee'] = list_committee + list_committee_other

        df.to_csv('./dataforthai_test2.csv', encoding='utf-8', index=False)
        
        # Save the current index value to the file
        with open(index_file, 'w') as file:
            file.write(str(i))
        
        sleep_time = random.uniform(1, 5)
        time.sleep(sleep_time)

        # Check if the break condition is met
        if i == break_parameter:
            break


IndexError: list index out of range

In [4]:
#Selenium

from selenium import webdriver
from selenium.webdriver.common.keys import Keys

driver = webdriver.Chrome("C:/Users/Warit/Webdrivers/chromedriver.exe")

driver.get("https://www.google.com")
search_box = driver.find_element_by_name("q")
search_box.send_keys("Hello, Selenium!")
search_box.send_keys(Keys.RETURN)

results = driver.find_elements_by_css_selector("div.rc")
for result in results:
    title = result.find_element_by_css_selector("h3").text
    link = result.find_element_by_css_selector("a").get_attribute("href")
    print(f"Title: {title}\nLink: {link}\n")

driver.quit()


C:\Users\Warit\AppData\Local\Temp\ipykernel_32088\365230037.py:6: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("C:/Users/Warit/Webdrivers/chromedriver.exe")


AttributeError: 'WebDriver' object has no attribute 'find_element_by_name'

In [4]:
#Test Proxy
import requests

# Define the proxy IP address
proxy = '35.213.91.45:80'

# Set up the requests session with the proxy
session = requests.Session()
session.proxies = {'http': proxy, 'https': proxy}

# Make requests using the session
response = session.get('https://example.com')


### Not in Use

In [16]:
#Try Proxies
import requests
import json
import numpy as np
import pandas as pd
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

# List of proxy IP addresses with HTTP protocol
proxies = [
    'http://139.144.24.46:8080',
    'http://129.153.157.63:3128',
    'http://35.213.91.45:80',
    # Add more proxy addresses as needed
]

df = pd.read_csv('./dataforthai.csv', dtype={'tax': str, 'tsic': str})

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if i == 100:
        break

    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']

        # Choose a random proxy from the list
        proxy = np.random.choice(proxies)

        req = requests.get(
            f'http://dataforthai.com/company/{tax}/',  # Use HTTP instead of HTTPS
            cookies=cookies,
            params=json.dumps(payload),
            proxies={'http': proxy}  # Pass the proxy address
        )

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        df['status'].iloc[i] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        df['date_register_thai'].iloc[i] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        df['capital'].iloc[i] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        
        address_element = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get()
        df['address'].iloc[i] = address_element.strip() if address_element else ''
        
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        df['list_committee'].iloc[i] = list_committee + list_committee_other

        df.to_csv('./dataforthai_test.csv', encoding='utf-8', index=False)


C:\Users\Warit\AppData\Local\Temp\ipykernel_17184\98335141.py:44: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['name_en'].iloc[i] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
C:\Users\Warit\AppData\Local\Temp\ipykernel_17184\98335141.py:46: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['business'].iloc[i] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
C:\Users\Warit\AppData\Local\Temp\ipykernel_17184\98335141.py:47: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata

ProxyError: HTTPConnectionPool(host='139.144.24.46', port=8080): Max retries exceeded with url: http://dataforthai.com/company/0135558015909/?%7B%7D (Caused by ProxyError('Cannot connect to proxy.', ConnectionResetError(10054, 'An existing connection was forcibly closed by the remote host', None, 10054, None)))

In [2]:
import requests
import json
import numpy as np
import pandas as pd
import time
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

df = pd.read_csv('./dataforthai.csv', dtype={'tax': str, 'tsic': str})

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# Create empty DataFrames for filled and unfilled records
filled_records = pd.DataFrame(columns=df.columns)
unfilled_records = pd.DataFrame(columns=df.columns)

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if i == 10:
        break
    
    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        v[1]['name_en'] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        v[1]['business'] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        v[1]['status'] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        v[1]['date_register_thai'] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        v[1]['capital'] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        v[1]['address'] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        v[1]['list_committee'] = list_committee + list_committee_other

        filled_records = filled_records.append(v[1])
    else:
        unfilled_records = unfilled_records.append(v[1])

# Save filled and unfilled records to separate CSV files
filled_records.to_csv('./filled_records.csv', encoding='utf-8', index=False)
unfilled_records.to_csv('./unfilled_records.csv', encoding='utf-8', index=False)

C:\Users\Warit\AppData\Local\Temp\ipykernel_26588\876896035.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  unfilled_records = unfilled_records.append(v[1])
C:\Users\Warit\AppData\Local\Temp\ipykernel_26588\876896035.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  unfilled_records = unfilled_records.append(v[1])
C:\Users\Warit\AppData\Local\Temp\ipykernel_26588\876896035.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  unfilled_records = unfilled_records.append(v[1])
C:\Users\Warit\AppData\Local\Temp\ipykernel_26588\876896035.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  unfilled_records = unfilled_records.append(v[

In [18]:
import requests
import json
import numpy as np
import pandas as pd
import time
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

df = pd.read_csv('./unfilled_records.csv', dtype={'tax': str, 'tsic': str})

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# Create empty DataFrames for filled and unfilled records
filled_records = pd.DataFrame(columns=df.columns)
unfilled_records = pd.DataFrame(columns=df.columns)

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        v[1]['name_en'] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        v[1]['business'] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        v[1]['status'] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        v[1]['date_register_thai'] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        v[1]['capital'] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        v[1]['address'] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        v[1]['list_committee'] = list_committee + list_committee_other

        filled_records = pd.concat([filled_records, v[1]], ignore_index=True)
    else:
        unfilled_records = pd.concat([unfilled_records, v[1]], ignore_index=True)

    # Display a message for every row processed
    print(f"Processed row {i+1}.")

# Save filled records to the existing filled_records.csv file
filled_records.to_csv('./filled_records.csv', encoding='utf-8', index=False, mode='a', header=False)

# Save unfilled records to the unfilled_records.csv file
unfilled_records.to_csv('./unfilled_records.csv', encoding='utf-8', index=False)


IndexError: list index out of range

In [19]:
#This work but output is not what expected
import requests
import json
import numpy as np
import pandas as pd
import time
from parsel import Selector
from bs4 import BeautifulSoup
from datetime import datetime

df = pd.read_csv('./unfilled_records.csv', dtype={'tax': str, 'tsic': str})

# PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
payload = {}
cookies = {"PHPSESSID": "fn9ugi97qsus6l52ekrcnto3j7"}

# Create empty DataFrames for filled and unfilled records
filled_records = pd.DataFrame(columns=df.columns)
unfilled_records = pd.DataFrame(columns=df.columns)

# PROCESS SCRAPING
for i, v in enumerate(df.iterrows()):
    if v[1]['name_en'] == '-':
        tax = v[1]['tax']
        tsic_code = v[1]['tsic']
        req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

        selector = Selector(text=req.text)
        created_at = datetime.now().isoformat()
        v[1]['name_en'] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
        container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
        v[1]['business'] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
        v[1]['status'] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
        v[1]['date_register_thai'] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
        v[1]['capital'] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
        v[1]['address'] = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
        list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
        list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
        v[1]['list_committee'] = list_committee + list_committee_other

        filled_records = pd.concat([filled_records, v[1]], ignore_index=True)

        # Save filled records to the filled_records.csv file after processing each row
        filled_records.to_csv('./filled_records.csv', encoding='utf-8', index=False, mode='a', header=False)
    else:
        unfilled_records = pd.concat([unfilled_records, v[1]], ignore_index=True)

    # Display a message for every row processed
    print(f"Processed row {i+1}.")

IndexError: list index out of range

### TEST

In [6]:
dft_df = pd.DataFrame()

In [22]:
tax = '0343564002992'
req = requests.get(f'https://dataforthai.com/company/{tax}/', cookies=cookies, params=json.dumps(payload))

In [23]:
### JUST TEST
soup = BeautifulSoup(req.text, 'html.parser')
with open('./soup2.html', 'w') as f:
    f.write(str(soup))

In [13]:
selector = Selector(text=req.text)
created_at = datetime.now().isoformat()
name_th = selector.xpath('//*/div[@id="main"]//h1/text()').get().strip()
name_en = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
business = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
tsic = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[2]').get().strip()
status = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
date_register_thai = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
capital = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
address = container_body.xpath('//*/table[6]/tr/td[2]/a/text()').get().strip()
list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]

temp_df = pd.DataFrame({'tax': tax, 'created_at': created_at, 'name_th': name_th, 'name_en':name_en, 'business':business, 'tsic':tsic, 'status':status, 'date_register_thai':date_register_thai, 'capital':capital, 'address':address, 'list_committee':[list_committee + list_committee_other]})

In [14]:
dft_df = dft_df.append(temp_df, ignore_index=True)
dft_df

tax                  created_at  \
0  0343564002992  2023-07-11T10:29:36.054968   
1  0343564002992  2023-07-11T10:34:11.877393   

                                         name_th  \
0  ห้างหุ้นส่วนจำกัด กลุ่มแปลงใหญ่ดอนเสาโฮงพัฒนา   
1  ห้างหุ้นส่วนจำกัด กลุ่มแปลงใหญ่ดอนเสาโฮงพัฒนา   

                                             name_en  \
0  BIG PLOT GROUP DON SAO HONG PHATTHANA LIMITED ...   
1  BIG PLOT GROUP DON SAO HONG PHATTHANA LIMITED ...   

                       business tsic               status date_register_thai  \
0  การปลูกข้าวโพดที่ใช้เมล็ดแก่       ยังดำเนินกิจการอยู่     29 เมษายน 2564   
1  การปลูกข้าวโพดที่ใช้เมล็ดแก่       ยังดำเนินกิจการอยู่     29 เมษายน 2564   

       capital                                            address  \
0  100,000 บาท  187 หมู่ที่ 30 ตำบลเมืองเดช อำเภอเดชอุดม จ.อุบ...   
1  100,000 บาท  187 หมู่ที่ 30 ตำบลเมืองเดช อำเภอเดชอุดม จ.อุบ...   

                                      list_committee  
0  [1. นายวิไลศักดิ์ พรมจันทึก, ลงหุ้นด้วยเงิน จำ...  
1  [1. นายวิไลศักดิ์ พรมจันทึก, ลงหุ้นด้วยเงิน จำ...

In [16]:
dft_df['list_committee'][1]

['1. นายวิไลศักดิ์ พรมจันทึก',
 'ลงหุ้นด้วยเงิน จำนวน 70,000.00 บาท',
 '2. นายสุจิขิต สำเภา',
 'ลงหุ้นด้วยเงิน จำนวน 30,000.00 บาท',
 '',
 'นายวิไลศักดิ์ พรมจันทึก']